In [3]:
from google.colab import drive
drive.mount('/content/drive')

shared_folder_path = '/content/drive/MyDrive/ds_project_dataset'

!cp -r "$shared_folder_path" .

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [4]:
import pandas as pd
import numpy as np
import cv2
import matplotlib.pyplot as plt
from tqdm import tqdm

from multiprocessing import Pool
from functools import partial

In [5]:
img_size = 224

In [6]:
def load_image(image_path, resize_shape=None):
    img = cv2.imread(image_path)
    if resize_shape is not None:
        img = cv2.resize(img, resize_shape)
    return img

def load_images_parallel(image_paths, n_jobs=4, resize_shape=None):
    with Pool(processes=n_jobs) as pool:
        func = partial(load_image, resize_shape=resize_shape)
        images = pool.map(func, image_paths)
    return np.array(images)

In [7]:
df = pd.read_csv('ds_project_dataset/articles.csv')

In [8]:
selected_categories = ['Garment Upper body', 'Underwear', 'Socks & Tights', 'Garment Lower body', 'Shoes', 'Garment Full body', 'Bags']
df = df[df['product_group_name'].isin(selected_categories)]

In [9]:
selected_categories = ['undefined', 'Unknown']
df = df[~df['perceived_colour_master_name'].isin(selected_categories)]

In [10]:
df['perceived_colour_master_name'] = df['perceived_colour_master_name'].replace(['Khaki green', 'Yellowish Green', 'Bluish Green', 'Lilac Purple'], ['Green', 'Green', 'Green', 'Purple'])

In [11]:
selected_categories = ['Other pattern', 'Unknown', 'Other structure']
df = df[~df['graphical_appearance_name'].isin(selected_categories)]

In [12]:
selected_categories = ['Ladieswear', 'Menswear', 'Divided']
df = df[df['index_group_name'].isin(selected_categories)]

In [13]:
df['subfolder'] = '0' + df['article_id'].astype(str).str[:2]
df['image_path'] = 'ds_project_dataset/images/' + df['subfolder'].str.strip() + '/0' + df['article_id'].astype(str) + '.jpg'

In [14]:
import os

valid_images = []
for index, row in tqdm(df[33000:].iterrows(), total=len(df[33000:])):
    if os.path.isfile(row['image_path']):
        valid_images.append(row)

df_valid_images = pd.DataFrame(valid_images)

100%|██████████| 21933/21933 [00:11<00:00, 1857.23it/s]


In [15]:
df_valid_images.shape

(11558, 27)

In [16]:
images = load_images_parallel(df_valid_images['image_path'].values, n_jobs=4, resize_shape=(img_size, img_size))

In [17]:
import tensorflow as tf

In [18]:
resnet_model = tf.keras.applications.ResNet50(
    include_top=False, weights='imagenet', pooling='avg')

# Define the image preprocessing pipeline
preprocess_input = tf.keras.applications.resnet50.preprocess_input

embeddings = []
for image in tqdm(images):
    # Add an extra batch dimension to the image
    image = np.expand_dims(image, axis=0)

    # Pass the image through the ResNet50 model
    features = resnet_model.predict(image)

    # Extract the embeddings from the output of the model
    embeddings.append(features.squeeze())

  0%|          | 0/11558 [00:00<?, ?it/s]

1/1 [==============================] - 1s 1s/step


  0%|          | 1/11558 [00:01<5:01:42,  1.57s/it]

1/1 [==============================] - 0s 240ms/step


  0%|          | 2/11558 [00:01<2:37:17,  1.22it/s]

...

100%|█████████▉| 11556/11558 [1:00:05<00:00,  2.83it/s]

1/1 [==============================] - 0s 215ms/step


100%|█████████▉| 11557/11558 [1:00:05<00:00,  3.03it/s]

1/1 [==============================] - 0s 217ms/step


100%|██████████| 11558/11558 [1:00:05<00:00,  3.21it/s]


In [19]:
new_df = pd.DataFrame(df_valid_images['article_id'])
new_df = new_df.join(df_valid_images['perceived_colour_master_name'])
new_df = new_df.join(df_valid_images['product_group_name'])
new_df = new_df.join(df_valid_images['graphical_appearance_name'])
new_df = new_df.join(df_valid_images['index_group_name'])

In [20]:
df_embed = new_df.assign(embeddings=embeddings)

In [21]:
df_embed

article_id perceived_colour_master_name  product_group_name  \
63119   738567009                        Green  Garment Lower body   
63120   738568003                        White  Garment Lower body   
63121   738569004                        Black  Garment Lower body   
63122   738569006                        Green  Garment Lower body   
63123   738571002                         Blue  Garment Lower body   
...           ...                          ...                 ...   
87117   826164005                         Mole   Garment Full body   
87118   826164006                        Black   Garment Full body   
87119   826164007                         Pink   Garment Full body   
87120   826164009                       Orange   Garment Full body   
87121   826164016                        White   Garment Full body   

      graphical_appearance_name index_group_name  \
63119                     Solid       Ladieswear   
63120                     Solid       Ladieswear   
63121                     Solid       Ladieswear   
63122                     Solid       Ladieswear   
63123                     Solid       Ladieswear   
...                         ...              ...   
87117                     Solid          Divided   
87118                     Solid          Divided   
87119                     Solid          Divided   
87120                     Solid          Divided   
87121                     Solid          Divided   

                                              embeddings  
63119  [0.63911676, 0.6077787, 0.10978092, 0.45921737...  
63120  [0.0, 0.12487834, 0.0, 0.0, 0.0, 0.8072149, 0....  
63121  [0.10748397, 0.7289399, 0.16909657, 1.0685954,...  
63122  [0.72341174, 1.1966548, 0.26805177, 0.67989707...  
63123  [0.66947657, 2.5759182, 0.858811, 0.98370594, ...  
...                                                  ...  
87117  [0.55072534, 6.3339887, 0.16771331, 0.05525394...  
87118  [0.5892944, 8.27611, 0.20807421, 0.0046255635,...  
87119  [0.32080218, 5.2998047, 0.08528918, 0.01577602...  
87120  [0.046470378, 8.77041, 0.10227045, 0.06753398,...  
87121  [0.67053473, 1.4959508, 0.060839552, 0.0121600...  

[11558 rows x 6 columns]

In [22]:
df_embed.to_csv('embeddings_dataframe4.csv', index=False)